# The [Modified Benedict-Webb-Rubin equation of state](https://en.wikipedia.org/wiki/Benedict–Webb–Rubin_equation) 
[Johnson, Zllweg, Gubbins, 
"The Lennard-Jones equation of state revisited",
Molecular Physics, 1993](Johnson_Lennard-Jones_1993.pdf)

implementing the parameters from Table 10

In [1]:
import numpy as np
np.set_printoptions(suppress=True)

In [2]:
import itertools
from bokeh.palettes import Viridis6
from bokeh.palettes import Category10_10 as palette

In [3]:
import bokeh.layouts  # gridplot

In [4]:
import bokeh.plotting 
bokeh.plotting.output_notebook()

Loading BokehJS ...

In [5]:
import glob
import os.path as op

**Reduced Units:**
  - residual Helmholtz free energy: $A^*_r = A_r/N\epsilon$
  - pressure: $P^* = P\sigma^3/\epsilon$
  - temperature: 
  
| Quantity    | Reduced Units      |  Real Units                      |
|-------------|--------------------|----------------------------------|
| temperature | $T^*=1$            | $T=119.8$ K                      |
| density     | $\rho^*=1.0$       | $\rho=1680$ kg/m$^3$             |
| time        | $\Delta t^*=0.005$ | $\Delta t=1.09\times 10^{-14}$ s |
| pressure    | $P^*=1$            | $P=41.9$ MPa                     |

$T^*=2.0$, to match Frenkel & Smit, bokeh.plotting.figure 6.2

In [6]:
T = 2.0

Modified Benedict-Webb-Rubin (MBWR) equation of state, Johnson et al. 1993, eq. (7):
$$ P^* = \rho^* T^* + \sum_{i=1}^8 a_i \rho^{*(i+1)} + \exp\left(-\gamma\rho^{*2}\right)\sum_{i=1}^{6}b_i \rho^{*(2i+1)} $$

1 nonlinear parameter:
  - $\gamma = 3$

In [7]:
gamma = 3

In [8]:
parameters = np.loadtxt('mbwr_eos.dat')
x = np.empty(len(parameters)+1) 
x[1:] = parameters[:, 1] # use 1 indexing for clarity
# print x

First 19 parameters, $a_1, \dots, a_8$:
  - $a_1 = x_1 T^* + x_2 \sqrt{T} + x_3 + x_4/T^* + x_5/T^{*2}$
  - $a_2 = x_6 T^* + x_7 + x_8/T^* + x_9/T^{*2}$
  - $a_3 = x_{10} T^* + x_{11} + x_{12}/T^*$
  - $a_4 = x_{13}$
  - $a_5 = x_{14}/T^* + x_{15}/T^{*2}$
  - $a_6 = x_{16}/T^*$
  - $a_7 = x_{17}/T^* + x_{18}/T^{*2}$
  - $a_8 = x_{19}/T^{*2}$

In [9]:
a1 = x[1]*T + x[2]*np.sqrt(T) + x[3] + x[4]/T + x[5]/T**2
a2 = x[6]*T + x[7] + x[8]/T + x[9]/T**2
a3 = x[10]*T + x[11] + x[12]/T
a4 = x[13]
a5 = x[14]/T + x[15]/T**2
a6 = x[16]/T
a7 = x[17]/T + x[18]/T**2
a8 = x[19]/T**2
a = np.empty(8)
a[:] = [a1, a2, a3, a4, a5, a6, a7, a8]

Last 13 parameters, $b_1, \dots, b_6$:
  - $b_1 = x_{20}/T^{*2} + x_{21}/T^{*3}$
  - $b_2 = x_{22}/T^{*2} + x_{23}/T^{*4}$
  - $b_3 = x_{24}/T^{*2} + x_{25}/T^{*3}$
  - $b_4 = x_{26}/T^{*2} + x_{27}/T^{*4}$
  - $b_5 = x_{28}/T^{*2} + x_{29}/T^{*3}$
  - $b_6 = x_{30}/T^{*2} + x_{31}/T^{*3} + x_{32}/T^{*4}$

In [10]:
b1 = x[20]/T**2 + x[21]/T**3
b2 = x[22]/T**2 + x[23]/T**4
b3 = x[24]/T**2 + x[25]/T**3
b4 = x[26]/T**2 + x[27]/T**4
b5 = x[28]/T**2 + x[29]/T**3
b6 = x[30]/T**2 + x[31]/T**3 + x[32]/T**4
b = np.empty(6)
b[:] = [b1, b2, b3, b4, b5, b6]

Modified Benedict-Webb-Rubin (MBWR) equation of state, Johnson et al. 1993, eq. (7):
$$ P^* = \rho^* T^* + \sum_{i=1}^8 a_i \rho^{*(i+1)} + \exp\left(-\gamma\rho^{*2}\right)\sum_{i=1}^{6}b_i \rho^{*(2i+1)} $$

In [11]:
density = np.linspace(0.1, 0.9)
f = np.exp(-gamma * density**2)

In [12]:
pressure200 = (
    density * T + 
    a1 * density**2 + 
    a2 * density**3 +
    a3 * density**4 + 
    a4 * density**5 +
    a5 * density**6 +
    a6 * density**7 +
    a7 * density**8 +
    a8 * density**9 +
    f * b1 * density**3 +
    f * b2 * density**5 +
    f * b3 * density**7 +
    f * b4 * density**9 +
    f * b5 * density**11 +
    f * b6 * density**13    
)

Validating implentation against Frenkel Smit, Figure 6.2 (data extracted using [WebPlotDigitizer](http://arohatgi.info/WebPlotDigitizer/)).

In [13]:
eos = np.loadtxt('fs_fig6.2_eos.csv', delimiter=',')
mc = np.loadtxt('fs_fig6.2_mc.csv', delimiter=',')
md = np.loadtxt('fs_fig6.2_md.csv', delimiter=',')

In [14]:
p = bokeh.plotting.figure(width=500, height=400, x_axis_label='Density',
           y_axis_label='Pressure')

p.line(density, pressure200, legend='eos Johnson', color=palette[0],
       line_width=2)
p.line(eos[:,0], eos[:,1], legend='eos F&S', color=palette[1],
       line_width=2)
p.circle(mc[:,0], mc[:,1], legend='MC F&S', size=12, 
         line_width=2, fill_alpha=0, color=palette[2])
p.square(md[:,0], md[:,1], legend='MD F&S', size=12, 
         line_width=2, fill_alpha=0, color=palette[3])

p.legend.location = 'top_left'
p.legend.click_policy = 'hide'

bokeh.plotting.show(p)

This demonstrates that my implementation of the Johnson's MBWR EOS agrees with Frenkel & Smit's EOS for a LJ fluid at $T^*=2.0$.

In [15]:
def mbwr_eos(T, density=None):
    a1 = x[1]*T + x[2]*np.sqrt(T) + x[3] + x[4]/T + x[5]/T**2
    a2 = x[6]*T + x[7] + x[8]/T + x[9]/T**2
    a3 = x[10]*T + x[11] + x[12]/T
    a4 = x[13]
    a5 = x[14]/T + x[15]/T**2
    a6 = x[16]/T
    a7 = x[17]/T + x[18]/T**2
    a8 = x[19]/T**2
     
    b1 = x[20]/T**2 + x[21]/T**3
    b2 = x[22]/T**2 + x[23]/T**4
    b3 = x[24]/T**2 + x[25]/T**3
    b4 = x[26]/T**2 + x[27]/T**4
    b5 = x[28]/T**2 + x[29]/T**3
    b6 = x[30]/T**2 + x[31]/T**3 + x[32]/T**4
    
    if density is None:
        density = np.linspace(0.0, 1.1)
        
    f = np.exp(-gamma * density**2)
    
    pressure = (
        density * T + 
        a1 * density**2 + 
        a2 * density**3 +
        a3 * density**4 + 
        a4 * density**5 +
        a5 * density**6 +
        a6 * density**7 +
        a7 * density**8 +
        a8 * density**9 +
        f * b1 * density**3 +
        f * b2 * density**5 +
        f * b3 * density**7 +
        f * b4 * density**9 +
        f * b5 * density**11 +
        f * b6 * density**13    
    )
    
    return density, pressure

In [16]:
assert np.allclose(pressure200, mbwr_eos(2.0, density)[1]
                  ), 'difference between function and original'

Repeat using $T^*=0.71$ ($T=85$ K), to match Liquid Argon data published by [Yarnell et al](Yarnell_Structure_1973.pdf).

In [17]:
pressure071 = mbwr_eos(0.71)[1]

In [18]:
argon_sigma = 3.405
argon_density = 0.0213 * argon_sigma ** 3
print(argon_sigma, argon_density)

3.405 0.8408740541624998


In [19]:
argon_pressure = mbwr_eos(0.71, density=argon_density)[1]

print(argon_pressure)

0.0280548649778


In [20]:
p = bokeh.plotting.figure(width=500, height=400, 
                          x_axis_label='Density',
                          y_axis_label='Pressure')
p.line(*mbwr_eos(2.0), legend="T=2.00")
p.line(*mbwr_eos(0.71), legend="T=0.71", line_color="firebrick")
p.legend.location='top_left'
bokeh.plotting.show(p)

While the $T=2.0$ case matches Figure 6.2 in Frenkel & Smit, I am skeptical about the $T=0.71$ case.  The negative pressure is somewhat surprising (the system is collapsing on itself?); I expect the range of densities cooresponding to negative pressures simply cannot be simulated using the same method.  

Johnson et al. present these parameters saying, "Parameters for the MBWR equation of state for the LJ fluid have been regressed for the temperature range $0.7\leq T^*\leq 6$ and covering the entire fluid range of densities."

### Load MD simulation data published by Johnson et al.

In [21]:
def rm_par(astr):
    return float(astr.split(b'(')[0])

In [22]:
data = np.genfromtxt('state_point.dat', dtype=None, names=True, converters={2:rm_par, 3:rm_par}, skip_header=3)

In [23]:
t20 = data[data['T']==2.0]
t14 = data[data['T']==1.4]
t10 = data[data['T']==1.0]
t07 = data[data['T']==0.7]

In [24]:
p = bokeh.plotting.figure(width=500, height=320, 
                          x_axis_label='Density', 
                          y_axis_label='Pressure')

p.line(*mbwr_eos(2.0), legend="T=2.00 EOS", color=palette[0])
p.line(*mbwr_eos(1.4), legend="T=1.4 EOS", color=palette[1])
p.line(*mbwr_eos(1.0), legend="T=1.0 EOS", color=palette[2])
p.line(*mbwr_eos(0.70), legend="T=0.70 EOS", color=palette[3])
p.line(*mbwr_eos(0.71), legend="T=0.71 EOS", color=palette[4])

p.circle(t20['p'], t20['P'], legend="T=2.00 Data", color=palette[5])
p.circle(t14['p'], t14['P'], legend="T=1.40 Data", color=palette[5])
p.circle(t10['p'], t10['P'], legend="T=1.00 Data", color=palette[6])
p.circle(t07['p'], t07['P'], legend="T=0.70 Data", color=palette[7])

p.legend.location = 'top_left'
p.legend.click_policy = 'hide'

bokeh.plotting.show(p)

As expected, the curves match the data from MD simulations, and there is even a simulation point that have a negative pressure, at density=0.8 and T=0.70.

### Compare Results from Our Simulations

In [25]:
N = 2048
T = 0.71

t071_P_runs = ['0p10', '0p11', '0p12', '0p13', '0p14', '0p15', 
               '0p16', '0p17', '0p18', '0p21', '0p23', '0p25', 
               '0p27']

t070_P_runs = ['m0p525', '0p00332', '0p40', '0p80', 
               '1p00', '1p14']

t200_P_runs = ['0.5', '1.0', '1.5', '2.0', '2.5', '3.0', '3.5', 
               '4.0', '4.5', '5.0', '5.5', '6.0', '6.5', '7.0', 
               '7.5', '8.0', '8.5', '9.0', '9.5']                                                                                                               
                 
t071_pressure = [float(val.replace('p', '.').replace('m', '-')) for val in t071_P_runs]
t070_pressure = [float(val.replace('p', '.').replace('m', '-')) for val in t070_P_runs]
t200_pressure = [float(val.replace('p', '.').replace('m', '-')) for val in t200_P_runs]

In [26]:
run_path = ['..', '..', 'cpp_simulations', 'lj_sphere_monomer', 'runs']

In [27]:
p_t070 = bokeh.plotting.figure(width=500, height=300, 
                               x_axis_label='Steps', 
                               y_axis_label='Density', 
                               title='T=0.70')

t070_density = []
t070_sigma = []
for P_val, color in zip(t070_P_runs, itertools.cycle(Viridis6)):

    path = op.join(*[run_path + ['p_{}'.format(P_val), 'output', 'box_length.txt']][0])
    P_dat = np.genfromtxt(path, names=True)
    print('{} shape: {}'.format(path, P_dat.shape))

    this_D = P_dat['density'][1000:].mean()
    this_sigma = P_dat['density'][1000:].std()
    
    t070_density.append(this_D)
    t070_sigma.append(this_sigma)
    
    p_t070.line(P_dat['step'], P_dat['density'], legend=P_val, color=color, alpha=0.05)
    p_t070.line(P_dat['step'][1000:], this_D, legend=P_val, color=color)
    p_t070.line(P_dat['step'][1000:], this_D+this_sigma, line_dash='dashed', legend=P_val, color=color)
    p_t070.line(P_dat['step'][1000:], this_D-this_sigma, line_dash='dashed', legend=P_val, color=color)
    
p_t070.legend.click_policy = 'hide'    
p_t070.legend.location='center_right'

../../cpp_simulations/lj_sphere_monomer/runs/p_m0p525/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p00332/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p40/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p80/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/p_1p00/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/p_1p14/output/box_length.txt shape: (5001,)


In [28]:
p_t071 = bokeh.plotting.figure(width=500, height=500, 
                               x_axis_label='Steps', 
                               y_axis_label='Density', 
                               title='T=0.71', 
                               x_range=p_t070.x_range)

t071_density = []
t071_sigma = []
for P_val, color in zip(t071_P_runs, itertools.cycle(Viridis6)):

    path = op.join(*[run_path + ['p_{}'.format(P_val), 'output', 
                                 'box_length.txt']][0])
    P_dat = np.genfromtxt(path, names=True)
    print('{} shape: {}'.format(path, P_dat.shape))
    
    this_D = P_dat['density'][1000:].mean()
    this_sigma = P_dat['density'][1000:].std()
    
    t071_density.append(this_D)
    t071_sigma.append(this_sigma)
    
    p_t071.line(P_dat['step'], P_dat['density'], legend=P_val, 
                color=color, alpha=0.05)
    p_t071.line(P_dat['step'][1000:], this_D, legend=P_val, 
                color=color)
    p_t071.line(P_dat['step'][1000:], this_D+this_sigma, 
                line_dash='dashed', legend=P_val, color=color)
    p_t071.line(P_dat['step'][1000:], this_D-this_sigma, 
                line_dash='dashed', legend=P_val, color=color)
    
p_t071.legend.click_policy = 'hide'
p_t071.legend.location='bottom_right'

../../cpp_simulations/lj_sphere_monomer/runs/p_0p10/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p11/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p12/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p13/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p14/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p15/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p16/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p17/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p18/output/box_length.txt shape: (5000,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p21/output/box_length.txt shape: (3820,)
../../cpp_simulations/lj_sphere_monomer/runs/p_0p23/output/box_length.txt shape: (3806,)
../../cpp_simulations

In [29]:
p_t200 = bokeh.plotting.figure(width=500, height=550, 
                               x_axis_label='Steps', 
                               y_axis_label='Density', 
                               title='T=2.00', 
                               x_range=p_t070.x_range)

t200_density = []
t200_sigma = []
for P_val, color in zip(t200_P_runs, itertools.cycle(Viridis6)):

    path = op.join(*[run_path + ['t2_p{}'.format(P_val), 'output', 
                                 'box_length.txt']][0])
    P_dat = np.genfromtxt(path, names=True)
    print('{} shape: {}'.format(path, P_dat.shape))

    this_D = P_dat['density'][1000:].mean()
    this_sigma = P_dat['density'][1000:].std()
    
    t200_density.append(this_D)
    t200_sigma.append(this_sigma)
    
    p_t200.line(P_dat['step'], P_dat['density'], legend=P_val, 
                color=color, alpha=0.05)
    p_t200.line(P_dat['step'][1000:], this_D, legend=P_val, 
                color=color)
    p_t200.line(P_dat['step'][1000:], this_D+this_sigma, 
                line_dash='dashed', legend=P_val, color=color)
    p_t200.line(P_dat['step'][1000:], this_D-this_sigma, 
                line_dash='dashed', legend=P_val, color=color)

p_t200.legend.click_policy = 'hide'
p_t200.legend.location='bottom_right'

../../cpp_simulations/lj_sphere_monomer/runs/t2_p0.5/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p1.0/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p1.5/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p2.0/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p2.5/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p3.0/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p3.5/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p4.0/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p4.5/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p5.0/output/box_length.txt shape: (5001,)
../../cpp_simulations/lj_sphere_monomer/runs/t2_p5.5/output/box_length.txt shape: (5001,)
../../cpp_

In [30]:
gp = bokeh.layouts.gridplot([[p_t070], [p_t071], [p_t200]])
bokeh.plotting.show(gp)

This demonstrates that by the $10000^\text{th}$ step, all systems have equilibrated.

In [31]:
box_length = 13.4618 * 3.405
min_q = 2 * np.pi / box_length
print(box_length, min_q)

45.837429 0.13707543036891504


In [32]:
def errorbar(fig, x, y, xerr=None, yerr=None, color='red', 
             point_kwargs={}, error_kwargs={}):

  fig.circle(x, y, color=color, **point_kwargs)

  if xerr:
      x_err_x = []
      x_err_y = []
      for px, py, err in zip(x, y, xerr):
          x_err_x.append((px - err, px + err))
          x_err_y.append((py, py))
      fig.multi_line(x_err_x, x_err_y, color=color, **error_kwargs)

  if yerr:
      y_err_x = []
      y_err_y = []
      for px, py, err in zip(x, y, yerr):
          y_err_x.append((px, px))
          y_err_y.append((py - err, py + err))
      fig.multi_line(y_err_x, y_err_y, color=color, **error_kwargs)

In [33]:
p = bokeh.plotting.figure(width=600, height=400, x_axis_label='Density',
                          y_axis_label='Pressure')

p.line(*mbwr_eos(2.0), legend="T=2.00 EOS", color=palette[0])
p.line(*mbwr_eos(1.4), legend="T=1.4 EOS", color=palette[1])
p.line(*mbwr_eos(1.0), legend="T=1.0 EOS", color=palette[2])
p.line(*mbwr_eos(0.70), legend="T=0.70 EOS", color=palette[3])
p.line(*mbwr_eos(0.71), legend="T=0.71 EOS", color=palette[4])

p.circle(t20['p'], t20['P'], legend="T=2.00 Data", color=palette[5])
p.circle(t14['p'], t14['P'], legend="T=1.40 Data", color=palette[5])
p.circle(t10['p'], t10['P'], legend="T=1.00 Data", color=palette[6])
p.circle(t07['p'], t07['P'], legend="T=0.70 Data", color=palette[7])

errorbar(p, t070_density, t070_pressure, yerr=t070_sigma, 
         color=palette[9],point_kwargs={'legend': 'T=0.70 Sim'})
errorbar(p, t071_density, t071_pressure, yerr=t071_sigma, 
         color=palette[0], point_kwargs={'legend': 'T=0.71 Sim'})
errorbar(p, t200_density, t200_pressure, yerr=t200_sigma, 
         color=palette[1], point_kwargs={'legend': 'T=2.00 Sim'})
p.circle(argon_density, argon_pressure, legend="argon state point", 
         color=palette[2])

p.legend.location = 'top_left'
p.legend.click_policy = 'hide'

bokeh.plotting.show(p)

For the most part, the simulations I ran are a reasonably close match to these results.  There seems to be a systematic shift up slightly.

Zoom in on the T=0.71 curve.

In [34]:
x_range = [0.8, 0.9]
y_range = [-0.5, 1.5]

p = bokeh.plotting.figure(width=600, height=400, x_axis_label='Density',
                          y_axis_label='Pressure', x_range=x_range, 
                          y_range=y_range)

p.line(*mbwr_eos(0.71, density=np.linspace(*x_range)), 
       legend="T=0.71 EOS", color=palette[0])
p.circle(argon_density, argon_pressure, legend="argon state point", 
         color=palette[1])
errorbar(p, t071_density, t071_pressure, yerr=t071_sigma, 
         color=palette[3], point_kwargs={'legend': 'T=0.71 Sim'})

p.legend.location='top_left'
bokeh.plotting.show(p)

All of the simulations are above the EOS line.  The "argon state point" is highlighting the density Hailiang was trying to simulate.

I am not certain which simulation the following data originates from, but it is comparing the Python and Fortran results.

In [35]:
p_gr_all = np.loadtxt('p_gr_all_stride1.dat')
p_gr_cut = np.loadtxt('p_gr_cutoff_stride1.dat')
f_gr_all = np.loadtxt('f_gr_all_stride1.dat')
f_gr_cut = np.loadtxt('f_gr_cutoff_stride1.dat')

In [36]:
p = bokeh.plotting.figure(width=600, height=400, x_axis_label='r', 
                          y_axis_label='g(r)')

p.line(p_gr_all[:, 0], p_gr_all[:, 1], color=palette[0],
       legend="python all")
p.line(p_gr_cut[:, 0], p_gr_cut[:, 1], color=palette[1],
       legend="python cut")
p.line(f_gr_all[:, 0], f_gr_all[:, 1], color=palette[2],
       legend="fortran all")
p.line(f_gr_cut[:, 0], f_gr_cut[:, 1], color=palette[3],
       legend="fortran cut")

p.legend.click_policy = "hide"
bokeh.plotting.show(p)

It looks like an indexing error existed in this data (though I think I later resolved this).

In [37]:
gr = np.loadtxt('argon_85K_gr.dat')

In [38]:
p = bokeh.plotting.figure(width=500, height=400, x_axis_label='r', 
                          y_axis_label='g(r)')

p.line(f_gr_cut[:, 0], f_gr_cut[:, 1]/f_gr_cut[-1, 1], 
       color=palette[1], legend="f cut")
p.line(gr[:, 0], gr[:, 1], color=palette[0], 
       legend="Experimental")

p.legend.click_policy = 'hide'
bokeh.plotting.show(p)

Here I have manually scaled the calculated results to be on the same scale as the experimental results.

In [39]:
dgr = gr[1:, 0] - gr[:-1, 0]
f_dgr = f_gr_cut[1:, 0] - f_gr_cut[:-1, 0]
dgr.min(), dgr.max(), f_dgr.min(), f_dgr.max()

(0.068099999999997607,
 0.06810000000000116,
 0.069203301801799455,
 0.069203301801810113)

In [40]:
dgr.min()/f_dgr.min()

0.98405709304215372